In [37]:
# this code will take the adoption model results that are the change in stock counts for each scenario compared to baseline
# and convert those to dollar savings based on avoided cost tables that Mike will provide

In [38]:
# eventually we will need to make this dynamic based on the cost test selected
# and have Mike create the various tables for avoided cost that the measure will carry with them
# but for now I will just make 10 copies of the 2026 results to use

#(Avoided cost Needs to be dependent on the cost test (Real discount rate will change)
#  now just an option but will keep real discount rate as 0.03 for all cost tests for now)

#the avoided cost tables are Cost by widget and year 

# When a widget is created the savings and costs for the entire lifetime are reported in that year 
# (the cost and savings are already discounted over the life time in the avoided costs inputs)

In [39]:
import pandas as pd
import numpy as np

In [40]:
# this code reads in the adoption model results for technical potential compared to baseline
competition_results_df = pd.read_pickle("050_input/competition_diff_adoption_results.pkl")
tech_results_df = pd.read_pickle("050_input/tech_diff_adoption_results.pkl")
# we Just care about the measures created
# the avoided costs metrics are at the measure level so the baseline energy is already removed from that calculation
# So we will drop the baseline and existing columns as we dont care what value they are
# but we do care about the efficient and top10 columns because they tell use where each equipment came from (stock and what it has become)

In [41]:
# this code drops the unneeded columns from tech_results_df any column with _baseline in it
columns_to_drop = [col for col in tech_results_df.columns if '_baseline' in col or '_below_baseline' in col]
tech_results_df = tech_results_df.drop(columns=columns_to_drop)

# Do the same for competition_results_df
columns_to_drop = [col for col in competition_results_df.columns if '_baseline' in col or '_below_baseline' in col]
competition_results_df = competition_results_df.drop(columns=columns_to_drop)

tech_results_df

competition_group electric_utility     gas_utility     building_type  \
0        refrigeration   test_utility_1  test_utility_1      multi_family   
1        refrigeration   test_utility_1  test_utility_1      multi_family   
2        refrigeration   test_utility_1  test_utility_1      multi_family   
3        refrigeration   test_utility_1  test_utility_1      multi_family   
4        refrigeration   test_utility_1  test_utility_1      multi_family   
...                ...              ...             ...               ...   
1435        whole_home   test_utility_2  test_utility_2  single_family_li   
1436        whole_home   test_utility_2  test_utility_2  single_family_li   
1437        whole_home   test_utility_2  test_utility_2  single_family_li   
1438        whole_home   test_utility_2  test_utility_2  single_family_li   
1439        whole_home   test_utility_2  test_utility_2  single_family_li   

      time  remaining_efficient_stock  remaining_top10_stock  \
0        0                        0.0               0.000000   
1        1                        0.0             600.000000   
2        2                        0.0            1100.000000   
3        3                        0.0            1516.666667   
4        4                        0.0            1863.888889   
...    ...                        ...                    ...   
1435    15                        0.0            1311.704233   
1436    16                        0.0            1328.086879   
1437    17                        0.0            1341.739072   
1438    18                        0.0            1353.115895   
1439    19                        0.0            1362.596580   

      ret_er_efficient_stock  ret_er_top10_stock  rob_efficient_stock  \
0                        0.0            0.000000                  0.0   
1                        0.0           24.000000                  0.0   
2                        0.0          139.680000                  0.0   
3                        0.0          298.590933                  0.0   
4                        0.0          471.857188                  0.0   
...                      ...                 ...                  ...   
1435                     0.0          615.073405                  0.0   
1436                     0.0          629.865330                  0.0   
1437                     0.0          642.259829                  0.0   
1438                     0.0          652.632934                  0.0   
1439                     0.0          661.306166                  0.0   

      rob_top10_stock  
0            0.000000  
1           12.000000  
2           19.840000  
3           57.628800  
4          109.539705  
...               ...  
1435       199.866284  
1436       205.623979  
1437       210.456008  
1438       214.504877  
1439       217.893425  

[1440 rows x 11 columns]

In [42]:
#this code calculates the change in stocks over time. It looks at the time column and calculated each row value example 1-2 
# Compute per-step adoptions (differences) on the long-form data for all dataframes
id_cols = ['competition_group', 'electric_utility', 'gas_utility', 'building_type', 'market', 'efficiency_level']

# Store results for both tech and competition
adoption_results = {}

# Process both dataframes
processed_dfs = {
    'tech': tech_results_df,
    'competition': competition_results_df
}

for name, results_df in processed_dfs.items():
    print(f"\nComputing adoptions for {name}_results_df...")
    
    # Recreate df_long the same way as before
    import re
    pattern = r'^(ret_er|rob|remaining)_(efficient|top10)_stock$'
    stock_cols = [c for c in results_df.columns if re.match(pattern, c)]
    df_long = results_df.melt(
        id_vars=['competition_group', 'electric_utility', 'gas_utility', 'building_type', 'time'],
        value_vars=stock_cols,
        var_name='market_eff',
        value_name='value'
    )
    df_long[['market','efficiency_level']] = df_long['market_eff'].str.extract(pattern)
    df_long = df_long.drop(columns=['market_eff'])
    
    # Sort and compute diffs
    df_long = df_long.sort_values(id_cols + ['time'])
    
    grouped = df_long.groupby(id_cols)['value']
    # Backward diff: value - previous value (NaN for first time)
    df_long['adoption'] = grouped.diff().fillna(0)
    
    # Pivot adoption (backward diff) to wide
    df_adopt_wide = df_long.pivot_table(
        index=id_cols,
        columns='time',
        values='adoption',
        aggfunc='first'
    ).reset_index()

    
    # Rename time columns to adopt_t_<time>
    def rename_time_cols(df, prefix='adopt_t'):
        df.columns.name = None
        new_cols = []
        for c in df.columns:
            if isinstance(c, (int, np.integer, float)):
                new_cols.append(f"{prefix}_{c}")
            else:
                new_cols.append(c)
        df.columns = new_cols
        return df
    
    df_adopt_wide = rename_time_cols(df_adopt_wide, prefix='adopt_t')
    
    print(f'Backward-diff adoption shape: {df_adopt_wide.shape}')
    
    adoption_results[name] = {
        'adopt_wide': df_adopt_wide
    }

# Display sample of tech results
print("\nTech adoption sample:")
display(adoption_results['tech']['adopt_wide'])



Computing adoptions for tech_results_df...
Backward-diff adoption shape: (432, 26)

Computing adoptions for competition_results_df...
Backward-diff adoption shape: (432, 26)

Tech adoption sample:


competition_group electric_utility     gas_utility     building_type  \
0       refrigeration             none            none      multi_family   
1       refrigeration             none            none      multi_family   
2       refrigeration             none            none      multi_family   
3       refrigeration             none            none      multi_family   
4       refrigeration             none            none      multi_family   
..                ...              ...             ...               ...   
427        whole_home   test_utility_2  test_utility_2  single_family_li   
428        whole_home   test_utility_2  test_utility_2  single_family_li   
429        whole_home   test_utility_2  test_utility_2  single_family_li   
430        whole_home   test_utility_2  test_utility_2  single_family_li   
431        whole_home   test_utility_2  test_utility_2  single_family_li   

        market efficiency_level  adopt_t_0  adopt_t_1   adopt_t_2   adopt_t_3  \
0    remaining        efficient        0.0   0.000000    0.000000    0.000000   
1    remaining            top10        0.0   0.000000    0.000000    0.000000   
2       ret_er        efficient        0.0   0.000000    0.000000    0.000000   
3       ret_er            top10        0.0   0.000000    0.000000    0.000000   
4          rob        efficient        0.0   0.000000    0.000000    0.000000   
..         ...              ...        ...        ...         ...         ...   
427  remaining            top10        0.0  78.333333  239.351852  199.459877   
428     ret_er        efficient        0.0   0.000000    0.000000    0.000000   
429     ret_er            top10        0.0  10.096296   19.651802   52.344322   
430        rob        efficient        0.0   0.000000    0.000000    0.000000   
431        rob            top10        0.0   5.048148    3.298123    6.226173   

     ...  adopt_t_10  adopt_t_11  adopt_t_12  adopt_t_13  adopt_t_14  \
0    ...    0.000000    0.000000    0.000000    0.000000    0.000000   
1    ...    0.000000    0.000000    0.000000    0.000000    0.000000   
2    ...    0.000000    0.000000    0.000000    0.000000    0.000000   
3    ...    0.000000    0.000000    0.000000    0.000000    0.000000   
4    ...    0.000000    0.000000    0.000000    0.000000    0.000000   
..   ...         ...         ...         ...         ...         ...   
427  ...   48.935882   40.771093   33.972968   28.309825   23.591194   
428  ...    0.000000    0.000000    0.000000    0.000000    0.000000   
429  ...   40.436169   34.574160   29.383594   24.859430   20.959794   
430  ...    0.000000    0.000000    0.000000    0.000000    0.000000   
431  ...   15.321864   13.209090   11.294206    9.598634    8.120745   

     adopt_t_15  adopt_t_16  adopt_t_17  adopt_t_18  adopt_t_19  
0      0.000000    0.000000    0.000000    0.000000    0.000000  
1      0.000000    0.000000    0.000000    0.000000    0.000000  
2      0.000000    0.000000    0.000000    0.000000    0.000000  
3      0.000000    0.000000    0.000000    0.000000    0.000000  
4      0.000000    0.000000    0.000000    0.000000    0.000000  
..          ...         ...         ...         ...         ...  
427   19.659219   16.382646   13.652193   11.376823    9.480685  
428    0.000000    0.000000    0.000000    0.000000    0.000000  
429   17.625596   14.791925   12.394499   10.373105    8.673232  
430    0.000000    0.000000    0.000000    0.000000    0.000000  
431    6.846865    5.757694    4.832029    4.048870    3.388548  

[432 rows x 26 columns]

In [43]:
# Save all adoption results to pickle and CSV files
for name in adoption_results.keys():
    df_adopt = adoption_results[name]['adopt_wide']
    output_pkl = f"050_output/{name}_adoption_changes.pkl"
    output_csv = f"050_output/{name}_adoption_changes.csv"
    df_adopt.to_pickle(output_pkl)
    df_adopt.to_csv(output_csv, index=False)
    print(f"Saved {name} adoption changes to {output_pkl} and {output_csv}")

Saved tech adoption changes to 050_output/tech_adoption_changes.pkl and 050_output/tech_adoption_changes.csv
Saved competition adoption changes to 050_output/competition_adoption_changes.pkl and 050_output/competition_adoption_changes.csv


In [44]:
# now we just sum up the total created because the stock doesnt tell us where they came from just the age of the asset
# only works in first year
# now with the summed total we know 2 percent of the Ret_ER population for that year was upgraded and 100 % of the rob was upgraded
# the rob to ret_er proportions to 1/eul and (1- 1/eul) * (1/3) * (0.02)


In [45]:
# this code collapses the market column into a total stock column and sums up all the numeric values 
# in the adoption model results df
collapsed_adoption_results = {}

for name in adoption_results.keys():
    df_adopt = adoption_results[name]['adopt_wide']
    
    # Get all the adopt_t columns (numeric columns)
    adopt_cols = [col for col in df_adopt.columns if col.startswith('adopt_t_')]
    
    # Group by all id columns except 'market' and sum the adoption values
    id_cols_no_market = ['competition_group', 'electric_utility', 'gas_utility', 'building_type', 'efficiency_level']
    
    df_collapsed = df_adopt.groupby(id_cols_no_market, as_index=False)[adopt_cols].sum()
    
    print(f"\n{name.capitalize()} collapsed adoption shape: {df_collapsed.shape}")
    collapsed_adoption_results[name] = df_collapsed

# Display sample
print("\nTech collapsed adoption sample:")
display(collapsed_adoption_results['tech'])
print("\nCompetition collapsed adoption sample:")
display(collapsed_adoption_results['competition'])


Tech collapsed adoption shape: (144, 25)

Competition collapsed adoption shape: (144, 25)

Tech collapsed adoption sample:


competition_group electric_utility     gas_utility     building_type  \
0       refrigeration             none            none      multi_family   
1       refrigeration             none            none      multi_family   
2       refrigeration             none            none   multi_family_li   
3       refrigeration             none            none   multi_family_li   
4       refrigeration             none            none     single_family   
..                ...              ...             ...               ...   
139        whole_home   test_utility_2  test_utility_2   multi_family_li   
140        whole_home   test_utility_2  test_utility_2     single_family   
141        whole_home   test_utility_2  test_utility_2     single_family   
142        whole_home   test_utility_2  test_utility_2  single_family_li   
143        whole_home   test_utility_2  test_utility_2  single_family_li   

    efficiency_level  adopt_t_0   adopt_t_1    adopt_t_2    adopt_t_3  \
0          efficient        0.0    0.000000     0.000000     0.000000   
1              top10        0.0    0.000000     0.000000     0.000000   
2          efficient        0.0    0.000000     0.000000     0.000000   
3              top10        0.0    0.000000     0.000000     0.000000   
4          efficient        0.0    0.000000     0.000000     0.000000   
..               ...        ...         ...          ...          ...   
139            top10        0.0   13.922222    39.066222    38.430055   
140        efficient        0.0    0.000000     0.000000     0.000000   
141            top10        0.0  546.944444  1534.744444  1509.752173   
142        efficient        0.0    0.000000     0.000000     0.000000   
143            top10        0.0   93.477778   262.301778   258.030371   

       adopt_t_4  ...  adopt_t_10  adopt_t_11  adopt_t_12  adopt_t_13  \
0       0.000000  ...    0.000000    0.000000    0.000000    0.000000   
1       0.000000  ...    0.000000    0.000000    0.000000    0.000000   
2       0.000000  ...    0.000000    0.000000    0.000000    0.000000   
3       0.000000  ...    0.000000    0.000000    0.000000    0.000000   
4       0.000000  ...    0.000000    0.000000    0.000000    0.000000   
..           ...  ...         ...         ...         ...         ...   
139    35.863295  ...   15.592711   13.188945   11.118199    9.348409   
140     0.000000  ...    0.000000    0.000000    0.000000    0.000000   
141  1408.915144  ...  612.570778  518.137107  436.786409  367.258925   
142     0.000000  ...    0.000000    0.000000    0.000000    0.000000   
143   240.796406  ...  104.693915   88.554342   74.650768   62.767889   

     adopt_t_14  adopt_t_15  adopt_t_16  adopt_t_17  adopt_t_18  adopt_t_19  
0      0.000000    0.000000    0.000000    0.000000    0.000000    0.000000  
1      0.000000    0.000000    0.000000    0.000000    0.000000    0.000000  
2      0.000000    0.000000    0.000000    0.000000    0.000000    0.000000  
3      0.000000    0.000000    0.000000    0.000000    0.000000    0.000000  
4      0.000000    0.000000    0.000000    0.000000    0.000000    0.000000  
..          ...         ...         ...         ...         ...         ...  
139    7.844726    6.572803    5.500550    4.598958    3.842374    3.208452  
140    0.000000    0.000000    0.000000    0.000000    0.000000    0.000000  
141  308.185668  258.217279  216.093046  180.673366  150.950412  126.046335  
142    0.000000    0.000000    0.000000    0.000000    0.000000    0.000000  
143   52.671732   44.131680   36.932266   30.878721   25.798798   21.542465  

[144 rows x 25 columns]


Competition collapsed adoption sample:


competition_group electric_utility     gas_utility     building_type  \
0       refrigeration             none            none      multi_family   
1       refrigeration             none            none      multi_family   
2       refrigeration             none            none   multi_family_li   
3       refrigeration             none            none   multi_family_li   
4       refrigeration             none            none     single_family   
..                ...              ...             ...               ...   
139        whole_home   test_utility_2  test_utility_2   multi_family_li   
140        whole_home   test_utility_2  test_utility_2     single_family   
141        whole_home   test_utility_2  test_utility_2     single_family   
142        whole_home   test_utility_2  test_utility_2  single_family_li   
143        whole_home   test_utility_2  test_utility_2  single_family_li   

    efficiency_level  adopt_t_0   adopt_t_1    adopt_t_2    adopt_t_3  \
0          efficient        0.0    0.000000     0.000000     0.000000   
1              top10        0.0    0.000000     0.000000     0.000000   
2          efficient        0.0    0.000000     0.000000     0.000000   
3              top10        0.0    0.000000     0.000000     0.000000   
4          efficient        0.0    0.000000     0.000000     0.000000   
..               ...        ...         ...          ...          ...   
139            top10        0.0    0.000000     0.000000     0.000000   
140        efficient        0.0  546.944444  1534.744444  1509.752173   
141            top10        0.0    0.000000     0.000000     0.000000   
142        efficient        0.0   93.477778   262.301778   258.030371   
143            top10        0.0    0.000000     0.000000     0.000000   

       adopt_t_4  ...  adopt_t_10  adopt_t_11  adopt_t_12  adopt_t_13  \
0       0.000000  ...    0.000000    0.000000    0.000000    0.000000   
1       0.000000  ...    0.000000    0.000000    0.000000    0.000000   
2       0.000000  ...    0.000000    0.000000    0.000000    0.000000   
3       0.000000  ...    0.000000    0.000000    0.000000    0.000000   
4       0.000000  ...    0.000000    0.000000    0.000000    0.000000   
..           ...  ...         ...         ...         ...         ...   
139     0.000000  ...    0.000000    0.000000    0.000000    0.000000   
140  1408.915144  ...  612.570778  518.137107  436.786409  367.258925   
141     0.000000  ...    0.000000    0.000000    0.000000    0.000000   
142   240.796406  ...  104.693915   88.554342   74.650768   62.767889   
143     0.000000  ...    0.000000    0.000000    0.000000    0.000000   

     adopt_t_14  adopt_t_15  adopt_t_16  adopt_t_17  adopt_t_18  adopt_t_19  
0      0.000000    0.000000    0.000000    0.000000    0.000000    0.000000  
1      0.000000    0.000000    0.000000    0.000000    0.000000    0.000000  
2      0.000000    0.000000    0.000000    0.000000    0.000000    0.000000  
3      0.000000    0.000000    0.000000    0.000000    0.000000    0.000000  
4      0.000000    0.000000    0.000000    0.000000    0.000000    0.000000  
..          ...         ...         ...         ...         ...         ...  
139    0.000000    0.000000    0.000000    0.000000    0.000000    0.000000  
140  308.185668  258.217279  216.093046  180.673366  150.950412  126.046335  
141    0.000000    0.000000    0.000000    0.000000    0.000000    0.000000  
142   52.671732   44.131680   36.932266   30.878721   25.798798   21.542465  
143    0.000000    0.000000    0.000000    0.000000    0.000000    0.000000  

[144 rows x 25 columns]

In [46]:
# we know that the relationship between ret_er and rob adoptions 
# will always be the same as defined in the adoption model
# so we can split the collapsed adoption results back into ret_er and rob components 
# these components will then be used to calculate the dollar savings based on avoided cost tables

In [47]:
def clean_column_names(df):
    df.columns = df.columns.str.lower().str.replace(' ', '_').str.replace('$', 'usd').str.replace('/', 'per').str.replace('&', 'and').str.replace('.', '')
    return df

In [69]:
#read in pickle file
# remember market is now an age thing not a replacement thing
df_yrs = pd.read_pickle("./030_input/df_yrs.pkl")
df_yrs
# filter df_years to remove any rows that have baseline or existing in the condition column
df_yrs = df_yrs[~df_yrs['condition'].str.contains('baseline|existing', case=False, na=False)]

# quickly make column efficiency_level based on the column condition_name. if condition_name contains 'efficient' then efficiency_level is 'efficient' else 'top10'
df_yrs['efficiency_level'] = np.where(df_yrs['condition'].str.contains('efficient', case=False, na=False), 'efficient', 'top10')
df_yrs = clean_column_names(df_yrs)
df_yrs

condition_name competition_group  \
14   refrigerator_electricity_efficient_residential     refrigeration   
15   refrigerator_electricity_efficient_residential     refrigeration   
16   refrigerator_electricity_efficient_residential     refrigeration   
17   refrigerator_electricity_efficient_residential     refrigeration   
18   refrigerator_electricity_efficient_residential     refrigeration   
..                                              ...               ...   
443      refrigerator_electricity_top10_residential     refrigeration   
444      refrigerator_electricity_top10_residential     refrigeration   
445      refrigerator_electricity_top10_residential     refrigeration   
446      refrigerator_electricity_top10_residential     refrigeration   
447      refrigerator_electricity_top10_residential     refrigeration   

      subgroup electric_utility     gas_utility    building_type  \
14   full_size   test_utility_1  test_utility_1    single_family   
15   full_size   test_utility_1  test_utility_2    single_family   
16   full_size   test_utility_2  test_utility_2    single_family   
17   full_size   test_utility_1            none    single_family   
18   full_size   test_utility_2            none    single_family   
..         ...              ...             ...              ...   
443  full_size   test_utility_2  test_utility_2  multi_family_li   
444  full_size   test_utility_1            none  multi_family_li   
445  full_size   test_utility_2            none  multi_family_li   
446  full_size             none  test_utility_1  multi_family_li   
447  full_size             none  test_utility_2  multi_family_li   

     measure_life_(yrs)  initial_count  \
14                 10.0        15000.0   
15                 10.0        30000.0   
16                 10.0        82500.0   
17                 10.0        15000.0   
18                 10.0        16500.0   
..                  ...            ...   
443                10.0         2100.0   
444                10.0          750.0   
445                10.0          750.0   
446                10.0          750.0   
447                10.0          750.0   

                                          condition     market  ...  sct_cost  \
14   refrigerator_electricity_efficient_residential        ROB  ...     880.0   
15   refrigerator_electricity_efficient_residential        ROB  ...     880.0   
16   refrigerator_electricity_efficient_residential        ROB  ...       NaN   
17   refrigerator_electricity_efficient_residential        ROB  ...       NaN   
18   refrigerator_electricity_efficient_residential        ROB  ...     960.0   
..                                              ...        ...  ...       ...   
443      refrigerator_electricity_top10_residential  REMAINING  ...       NaN   
444      refrigerator_electricity_top10_residential  REMAINING  ...       NaN   
445      refrigerator_electricity_top10_residential  REMAINING  ...       NaN   
446      refrigerator_electricity_top10_residential  REMAINING  ...       NaN   
447      refrigerator_electricity_top10_residential  REMAINING  ...       NaN   

    sct_benefit   sct_bcr rim_cost rim_benefit   rim_bcr  pct_cost  \
14    96.262263  0.109389    560.0       320.0  0.571429     400.0   
15   104.792465  0.119082    660.0       320.0  0.484848     400.0   
16          NaN       NaN      NaN         NaN       NaN       NaN   
17          NaN       NaN      NaN         NaN       NaN       NaN   
18   113.106047  0.117819    540.0       320.0  0.592593     400.0   
..          ...       ...      ...         ...       ...       ...   
443         NaN       NaN      NaN         NaN       NaN       NaN   
444         NaN       NaN      NaN         NaN       NaN       NaN   
445         NaN       NaN      NaN         NaN       NaN       NaN   
446         NaN       NaN      NaN         NaN       NaN       NaN   
447         NaN       NaN      NaN         NaN       NaN       NaN   

     pct_benefit   pct_b

In [49]:
# make a unique list every competition group and thir EUL
unique_competition_groups = df_yrs[['competition_group', 'measure_life_(yrs)']].drop_duplicates()
# this might need to be expanded to include the subgroups

In [ ]:
# join the unique competition groups and their EUL to the collapsed adoption results
# and use EUL in the split calculation total_stock cancels out so we dont need it
# Starting from total stock formulas:
#   rob_adopted = total_stock * (1/EUL)
#   ret_er_adopted = total_stock * (1 - 1/EUL) * (1/3) * 0.02
#   total_adopted = rob_adopted + ret_er_adopted
# We can derive the proportions to split total_adopted back into components
for name in collapsed_adoption_results.keys():
    df_collapsed = collapsed_adoption_results[name]
    # Merge with unique competition groups to get EUL
    df_collapsed = df_collapsed.merge(unique_competition_groups, on='competition_group', how='left')
    
    # Calculate the proportion factors
    # rob_factor = (1/EUL)
    # ret_er_factor = (1 - 1/EUL) * (1/3) * 0.02
    # total_factor = rob_factor + ret_er_factor (this is what total_adopted/total_stock equals)
    rob_factor = 1 / df_collapsed['measure_life_(yrs)']
    ret_er_factor = (1 - 1/df_collapsed['measure_life_(yrs)']) * (1/3) * 0.02
    total_factor = rob_factor + ret_er_factor
    
    # Split each adopt_t_<time> column into ret_er and rob components
    adopt_cols = [col for col in df_collapsed.columns if col.startswith('adopt_t_')]
    
    for col in adopt_cols:
        # ROB allocation: total_adopted * (rob_factor / total_factor)
        df_collapsed[f'rob_{col}'] = df_collapsed[col] * (rob_factor / total_factor)
        
        # RET_ER allocation: total_adopted * (ret_er_factor / total_factor)
        df_collapsed[f'ret_er_{col}'] = df_collapsed[col] * (ret_er_factor / total_factor)
    
    # Drop the original collapsed adopt_t_<time> columns
    df_collapsed = df_collapsed.drop(columns=adopt_cols)
    
    # Update the collapsed adoption results
    collapsed_adoption_results[name] = df_collapsed

    print(f"\n{name.capitalize()} split adoption shape: {df_collapsed.shape}")
df_collapsed


Tech split adoption shape: (144, 46)

Competition split adoption shape: (144, 46)


competition_group electric_utility     gas_utility     building_type  \
0       refrigeration             none            none      multi_family   
1       refrigeration             none            none      multi_family   
2       refrigeration             none            none   multi_family_li   
3       refrigeration             none            none   multi_family_li   
4       refrigeration             none            none     single_family   
..                ...              ...             ...               ...   
139        whole_home   test_utility_2  test_utility_2   multi_family_li   
140        whole_home   test_utility_2  test_utility_2     single_family   
141        whole_home   test_utility_2  test_utility_2     single_family   
142        whole_home   test_utility_2  test_utility_2  single_family_li   
143        whole_home   test_utility_2  test_utility_2  single_family_li   

    efficiency_level  measure_life_(yrs)  rob_adopt_t_0  ret_er_adopt_t_0  \
0          efficient                10.0            0.0               0.0   
1              top10                10.0            0.0               0.0   
2          efficient                10.0            0.0               0.0   
3              top10                10.0            0.0               0.0   
4          efficient                10.0            0.0               0.0   
..               ...                 ...            ...               ...   
139            top10                30.0            0.0               0.0   
140        efficient                30.0            0.0               0.0   
141            top10                30.0            0.0               0.0   
142        efficient                30.0            0.0               0.0   
143            top10                30.0            0.0               0.0   

     rob_adopt_t_1  ret_er_adopt_t_1  ...  rob_adopt_t_15  ret_er_adopt_t_15  \
0         0.000000          0.000000  ...        0.000000           0.000000   
1         0.000000          0.000000  ...        0.000000           0.000000   
2         0.000000          0.000000  ...        0.000000           0.000000   
3         0.000000          0.000000  ...        0.000000           0.000000   
4         0.000000          0.000000  ...        0.000000           0.000000   
..             ...               ...  ...             ...                ...   
139       0.000000          0.000000  ...        0.000000           0.000000   
140     458.333333         88.611111  ...      216.383194          41.834084   
141       0.000000          0.000000  ...        0.000000           0.000000   
142      78.333333         15.144444  ...       36.981855           7.149825   
143       0.000000          0.000000  ...        0.000000           0.000000   

     rob_adopt_t_16  ret_er_adopt_t_16  rob_adopt_t_17  ret_er_adopt_t_17  \
0          0.000000           0.000000        0.000000           0.000000   
1          0.000000           0.000000        0.000000           0.000000   
2          0.000000           0.000000        0.000000           0.000000   
3          0.000000           0.000000        0.000000           0.000000   
4          0.000000           0.000000        0.000000           0.000000   
..              ...                ...             ...                ...   
139        0.000000           0.000000        0.000000           0.000000   
140      181.083558          35.009488      151.402262          29.271104   
141        0.000000           0.000000        0.000000           0.000000   
142       30.948826           5.983440       25.876023           5.002698   
143        0.000000           0.000000        0.000000           0.000000   

     rob_adopt_t_18  ret_er_adopt_t_18  rob_adopt_t_19  ret_er_adopt_t_19  
0          0.000000           0.000000        0.000000           0.000000  
1          0.000000           0.000000        0.000000           0.000000  
2          0.000000           0.000000        0.0000

In [51]:
# this code takes the df_collapsed and splits it back into ret_er and rob components for every time column
# the time columns are currently called adopt_t_<time>
# the new columns will be called ret_er_adopt_t_<time> and rob_adopt_t_<time>
# 
# Allocation logic (derived from total stock relationships):
# From the stock model we know:
#   rob_adopted = total_stock * (1/EUL)                               [100% of ROB population upgraded]
#   ret_er_adopted = total_stock * (1 - 1/EUL) * (1/3) * 0.02        [2% of RET_ER population upgraded]
# 
# Since total_adopted = rob_adopted + ret_er_adopted, we can derive:
#   rob_proportion = (1/EUL) / [(1/EUL) + (1 - 1/EUL) * (1/3) * 0.02]
#   ret_er_proportion = [(1 - 1/EUL) * (1/3) * 0.02] / [(1/EUL) + (1 - 1/EUL) * (1/3) * 0.02]
# 
# This allows us to split total_adopted back into its components without needing total_stock

In [55]:
# this code now makes the adoption results into columns we can join with avoided cost tables
# first we need to convert df_collapsed to have the correct column names
# the columns ret_er_adopt_t_<time> and rob_adopt_t_<time> will be put into rows with the column header Market and values ret_er and rob respectively
# Time stays in column headers for a wide format

reshaped_adoption_results = {}

for name in collapsed_adoption_results.keys():
    df_collapsed = collapsed_adoption_results[name]
    
    # Get the ID columns (everything except the adopt columns and measure_life)
    id_cols = ['competition_group', 'electric_utility', 'gas_utility', 'building_type', 'efficiency_level', 'measure_life_(yrs)']
    
    # Separate ret_er and rob columns
    ret_er_cols = [col for col in df_collapsed.columns if col.startswith('ret_er_adopt_t_')]
    rob_cols = [col for col in df_collapsed.columns if col.startswith('rob_adopt_t_')]
    
    # Create ret_er dataframe with market column
    df_ret_er = df_collapsed[id_cols + ret_er_cols].copy()
    df_ret_er['market'] = 'ret_er'
    # Rename columns to remove ret_er_ prefix (ret_er_adopt_t_2026 -> adopt_t_2026)
    rename_dict = {col: col.replace('ret_er_', '') for col in ret_er_cols}
    df_ret_er = df_ret_er.rename(columns=rename_dict)
    
    # Create rob dataframe with market column
    df_rob = df_collapsed[id_cols + rob_cols].copy()
    df_rob['market'] = 'rob'
    # Rename columns to remove rob_ prefix (rob_adopt_t_2026 -> adopt_t_2026)
    rename_dict = {col: col.replace('rob_', '') for col in rob_cols}
    df_rob = df_rob.rename(columns=rename_dict)
    
    # Combine ret_er and rob
    df_reshaped = pd.concat([df_ret_er, df_rob], ignore_index=True)
    
    # Reorder columns: id columns, market, then all time columns
    time_cols = [col for col in df_reshaped.columns if col.startswith('adopt_t_')]
    df_reshaped = df_reshaped[id_cols + ['market'] + sorted(time_cols)]
    
    reshaped_adoption_results[name] = df_reshaped
    print(f"\n{name.capitalize()} reshaped adoption shape: {df_reshaped.shape}")

# Display sample
print("\nTech reshaped adoption sample:")
display(reshaped_adoption_results['tech'])
print("\nCompetition reshaped adoption sample:")
display(reshaped_adoption_results['competition'])


Tech reshaped adoption shape: (288, 27)

Competition reshaped adoption shape: (288, 27)

Tech reshaped adoption sample:


competition_group electric_utility     gas_utility     building_type  \
0       refrigeration             none            none      multi_family   
1       refrigeration             none            none      multi_family   
2       refrigeration             none            none   multi_family_li   
3       refrigeration             none            none   multi_family_li   
4       refrigeration             none            none     single_family   
..                ...              ...             ...               ...   
283        whole_home   test_utility_2  test_utility_2   multi_family_li   
284        whole_home   test_utility_2  test_utility_2     single_family   
285        whole_home   test_utility_2  test_utility_2     single_family   
286        whole_home   test_utility_2  test_utility_2  single_family_li   
287        whole_home   test_utility_2  test_utility_2  single_family_li   

    efficiency_level  measure_life_(yrs)  market  adopt_t_0   adopt_t_1  \
0          efficient                10.0  ret_er        0.0    0.000000   
1              top10                10.0  ret_er        0.0    0.000000   
2          efficient                10.0  ret_er        0.0    0.000000   
3              top10                10.0  ret_er        0.0    0.000000   
4          efficient                10.0  ret_er        0.0    0.000000   
..               ...                 ...     ...        ...         ...   
283            top10                30.0     rob        0.0   11.666667   
284        efficient                30.0     rob        0.0    0.000000   
285            top10                30.0     rob        0.0  458.333333   
286        efficient                30.0     rob        0.0    0.000000   
287            top10                30.0     rob        0.0   78.333333   

     adopt_t_10  ...  adopt_t_18  adopt_t_19    adopt_t_2    adopt_t_3  \
0      0.000000  ...    0.000000    0.000000     0.000000     0.000000   
1      0.000000  ...    0.000000    0.000000     0.000000     0.000000   
2      0.000000  ...    0.000000    0.000000     0.000000     0.000000   
3      0.000000  ...    0.000000    0.000000     0.000000     0.000000   
4      0.000000  ...    0.000000    0.000000     0.000000     0.000000   
..          ...  ...         ...         ...          ...          ...   
283   13.066517  ...    3.219867    2.688647    32.737058    32.203957   
284    0.000000  ...    0.000000    0.000000     0.000000     0.000000   
285  513.327468  ...  126.494758  105.625421  1286.098696  1265.155452   
286    0.000000  ...    0.000000    0.000000     0.000000     0.000000   
287   87.732331  ...   21.619104   18.052345   219.805959   216.226568   

       adopt_t_4    adopt_t_5   adopt_t_6   adopt_t_7   adopt_t_8   adopt_t_9  
0       0.000000     0.000000    0.000000    0.000000    0.000000    0.000000  
1       0.000000     0.000000    0.000000    0.000000    0.000000    0.000000  
2       0.000000     0.000000    0.000000    0.000000    0.000000    0.000000  
3       0.000000     0.000000    0.000000    0.000000    0.000000    0.000000  
4       0.000000     0.000000    0.000000    0.000000    0.000000    0.000000  
..           ...          ...         ...         ...         ...         ...  
283    30.053040    27.145588   23.994229   20.892157   17.996148   15.379655  
284     0.000000     0.000000    0.000000    0.000000    0.000000    0.000000  
285  1180.655148  1066.433797  942.630442  820.763300  706.991533  604.200726  
286     0.000000     0.000000    0.000000    0.000000    0.000000    0.000000  
287   201.784698   182.263231  161.104112  140.275910  120.831280  103.263397  

[288 rows x 27 columns]


Competition reshaped adoption sample:


competition_group electric_utility     gas_utility     building_type  \
0       refrigeration             none            none      multi_family   
1       refrigeration             none            none      multi_family   
2       refrigeration             none            none   multi_family_li   
3       refrigeration             none            none   multi_family_li   
4       refrigeration             none            none     single_family   
..                ...              ...             ...               ...   
283        whole_home   test_utility_2  test_utility_2   multi_family_li   
284        whole_home   test_utility_2  test_utility_2     single_family   
285        whole_home   test_utility_2  test_utility_2     single_family   
286        whole_home   test_utility_2  test_utility_2  single_family_li   
287        whole_home   test_utility_2  test_utility_2  single_family_li   

    efficiency_level  measure_life_(yrs)  market  adopt_t_0   adopt_t_1  \
0          efficient                10.0  ret_er        0.0    0.000000   
1              top10                10.0  ret_er        0.0    0.000000   
2          efficient                10.0  ret_er        0.0    0.000000   
3              top10                10.0  ret_er        0.0    0.000000   
4          efficient                10.0  ret_er        0.0    0.000000   
..               ...                 ...     ...        ...         ...   
283            top10                30.0     rob        0.0    0.000000   
284        efficient                30.0     rob        0.0  458.333333   
285            top10                30.0     rob        0.0    0.000000   
286        efficient                30.0     rob        0.0   78.333333   
287            top10                30.0     rob        0.0    0.000000   

     adopt_t_10  ...  adopt_t_18  adopt_t_19    adopt_t_2    adopt_t_3  \
0      0.000000  ...    0.000000    0.000000     0.000000     0.000000   
1      0.000000  ...    0.000000    0.000000     0.000000     0.000000   
2      0.000000  ...    0.000000    0.000000     0.000000     0.000000   
3      0.000000  ...    0.000000    0.000000     0.000000     0.000000   
4      0.000000  ...    0.000000    0.000000     0.000000     0.000000   
..          ...  ...         ...         ...          ...          ...   
283    0.000000  ...    0.000000    0.000000     0.000000     0.000000   
284  513.327468  ...  126.494758  105.625421  1286.098696  1265.155452   
285    0.000000  ...    0.000000    0.000000     0.000000     0.000000   
286   87.732331  ...   21.619104   18.052345   219.805959   216.226568   
287    0.000000  ...    0.000000    0.000000     0.000000     0.000000   

       adopt_t_4    adopt_t_5   adopt_t_6  adopt_t_7   adopt_t_8   adopt_t_9  
0       0.000000     0.000000    0.000000    0.00000    0.000000    0.000000  
1       0.000000     0.000000    0.000000    0.00000    0.000000    0.000000  
2       0.000000     0.000000    0.000000    0.00000    0.000000    0.000000  
3       0.000000     0.000000    0.000000    0.00000    0.000000    0.000000  
4       0.000000     0.000000    0.000000    0.00000    0.000000    0.000000  
..           ...          ...         ...        ...         ...         ...  
283     0.000000     0.000000    0.000000    0.00000    0.000000    0.000000  
284  1180.655148  1066.433797  942.630442  820.76330  706.991533  604.200726  
285     0.000000     0.000000    0.000000    0.00000    0.000000    0.000000  
286   201.784698   182.263231  161.104112  140.27591  120.831280  103.263397  
287     0.000000     0.000000    0.000000    0.00000    0.000000    0.000000  

[288 rows x 27 columns]

In [67]:
# We will join the reshaped adoption results with df_yrs (avoided cost data)
# Join keys: competition_group, electric_utility, gas_utility, building_type, efficiency_level, subgroup, market
# First, let's check what columns are in df_yrs and what we need to add to reshaped_adoption_results

print("df_yrs columns:")
print(df_yrs.columns.tolist())
print(f"\ndf_yrs shape: {df_yrs.shape}")
print("\ndf_yrs sample:")
display(df_yrs.head())

print("\n" + "="*80 + "\n")

print("reshaped_adoption_results['tech'] columns:")
print(reshaped_adoption_results['tech'].columns.tolist())
print(f"\nreshaped_adoption_results['tech'] shape: {reshaped_adoption_results['tech'].shape}")
print("\nreshaped_adoption_results['tech'] sample:")
display(reshaped_adoption_results['tech'])

df_yrs columns:
['condition_name', 'competition_group', 'subgroup', 'electric_utility', 'gas_utility', 'building_type', 'measure_life_(yrs)', 'initial_count', 'condition', 'market', 'count', 'measure_name', 'sector', 'program', 'baseline_condition', 'efficient_condition', 'incremental_installed_cost_year_1', 'deferred_replacement_install_cost', 'annual_oandm_cost', 'annual_electric_energy_saved_(kwh)_-_refrigeration', 'annual_natural_gas_energy_saved_(mmbtu)_-_refrigeration', 'annual_propane_energy_saved_(mmbtu)_-_refrigeration', 'annual_heating_oil_energy_saved_(mmbtu)_-_refrigeration', 'annual_electric_energy_saved_(kwh)_-_other', 'annual_natural_gas_energy_saved_(mmbtu)_-_other', 'annual_propane_energy_saved_(mmbtu)_-_other', 'annual_heating_oil_energy_saved_(mmbtu)_-_other', 'water_savings_(gallons)', 'kw-kwh_ratio', 'measure_incremental_cost', 'demand_ratio', 'deferred_replacement_credit_value', 'measure_water_savings', 'measure_electric_energy_savings', 'measure_natural_gas_savin

condition_name competition_group   subgroup  \
0  refrigerator_electricity_existing_residential     refrigeration  full_size   
1  refrigerator_electricity_existing_residential     refrigeration  full_size   
2  refrigerator_electricity_existing_residential     refrigeration  full_size   
3  refrigerator_electricity_existing_residential     refrigeration  full_size   
4  refrigerator_electricity_existing_residential     refrigeration  full_size   

  electric_utility     gas_utility  building_type  measure_life_(yrs)  \
0   test_utility_1  test_utility_1  single_family                10.0   
1   test_utility_1  test_utility_2  single_family                10.0   
2   test_utility_2  test_utility_2  single_family                10.0   
3   test_utility_1            none  single_family                10.0   
4   test_utility_2            none  single_family                10.0   

   initial_count                                      condition market  ...  \
0        10000.0  refrigerator_electricity_existing_residential    ROB  ...   
1        20000.0  refrigerator_electricity_existing_residential    ROB  ...   
2        55000.0  refrigerator_electricity_existing_residential    ROB  ...   
3        10000.0  refrigerator_electricity_existing_residential    ROB  ...   
4        11000.0  refrigerator_electricity_existing_residential    ROB  ...   

   TRC_BCR SCT_cost SCT_benefit SCT_BCR RIM_cost RIM_benefit  RIM_BCR  \
0      NaN      NaN         NaN     NaN      NaN         NaN      NaN   
1      NaN      NaN         NaN     NaN      NaN         NaN      NaN   
2      NaN      NaN         NaN     NaN      NaN         NaN      NaN   
3      NaN      NaN         NaN     NaN      NaN         NaN      NaN   
4      NaN      NaN         NaN     NaN      NaN         NaN      NaN   

   PCT_cost  PCT_benefit  PCT_BCR  
0       NaN          NaN      NaN  
1       NaN          NaN      NaN  
2       NaN          NaN      NaN  
3       NaN          NaN      NaN  
4       NaN          NaN      NaN  

[5 rows x 105 columns]



reshaped_adoption_results['tech'] columns:
['competition_group', 'electric_utility', 'gas_utility', 'building_type', 'efficiency_level', 'measure_life_(yrs)', 'market', 'adopt_t_0', 'adopt_t_1', 'adopt_t_10', 'adopt_t_11', 'adopt_t_12', 'adopt_t_13', 'adopt_t_14', 'adopt_t_15', 'adopt_t_16', 'adopt_t_17', 'adopt_t_18', 'adopt_t_19', 'adopt_t_2', 'adopt_t_3', 'adopt_t_4', 'adopt_t_5', 'adopt_t_6', 'adopt_t_7', 'adopt_t_8', 'adopt_t_9']

reshaped_adoption_results['tech'] shape: (288, 27)

reshaped_adoption_results['tech'] sample:


competition_group electric_utility     gas_utility     building_type  \
0       refrigeration             none            none      multi_family   
1       refrigeration             none            none      multi_family   
2       refrigeration             none            none   multi_family_li   
3       refrigeration             none            none   multi_family_li   
4       refrigeration             none            none     single_family   
..                ...              ...             ...               ...   
283        whole_home   test_utility_2  test_utility_2   multi_family_li   
284        whole_home   test_utility_2  test_utility_2     single_family   
285        whole_home   test_utility_2  test_utility_2     single_family   
286        whole_home   test_utility_2  test_utility_2  single_family_li   
287        whole_home   test_utility_2  test_utility_2  single_family_li   

    efficiency_level  measure_life_(yrs)  market  adopt_t_0   adopt_t_1  \
0          efficient                10.0  ret_er        0.0    0.000000   
1              top10                10.0  ret_er        0.0    0.000000   
2          efficient                10.0  ret_er        0.0    0.000000   
3              top10                10.0  ret_er        0.0    0.000000   
4          efficient                10.0  ret_er        0.0    0.000000   
..               ...                 ...     ...        ...         ...   
283            top10                30.0     rob        0.0   11.666667   
284        efficient                30.0     rob        0.0    0.000000   
285            top10                30.0     rob        0.0  458.333333   
286        efficient                30.0     rob        0.0    0.000000   
287            top10                30.0     rob        0.0   78.333333   

     adopt_t_10  ...  adopt_t_18  adopt_t_19    adopt_t_2    adopt_t_3  \
0      0.000000  ...    0.000000    0.000000     0.000000     0.000000   
1      0.000000  ...    0.000000    0.000000     0.000000     0.000000   
2      0.000000  ...    0.000000    0.000000     0.000000     0.000000   
3      0.000000  ...    0.000000    0.000000     0.000000     0.000000   
4      0.000000  ...    0.000000    0.000000     0.000000     0.000000   
..          ...  ...         ...         ...          ...          ...   
283   13.066517  ...    3.219867    2.688647    32.737058    32.203957   
284    0.000000  ...    0.000000    0.000000     0.000000     0.000000   
285  513.327468  ...  126.494758  105.625421  1286.098696  1265.155452   
286    0.000000  ...    0.000000    0.000000     0.000000     0.000000   
287   87.732331  ...   21.619104   18.052345   219.805959   216.226568   

       adopt_t_4    adopt_t_5   adopt_t_6   adopt_t_7   adopt_t_8   adopt_t_9  
0       0.000000     0.000000    0.000000    0.000000    0.000000    0.000000  
1       0.000000     0.000000    0.000000    0.000000    0.000000    0.000000  
2       0.000000     0.000000    0.000000    0.000000    0.000000    0.000000  
3       0.000000     0.000000    0.000000    0.000000    0.000000    0.000000  
4       0.000000     0.000000    0.000000    0.000000    0.000000    0.000000  
..           ...          ...         ...         ...         ...         ...  
283    30.053040    27.145588   23.994229   20.892157   17.996148   15.379655  
284     0.000000     0.000000    0.000000    0.000000    0.000000    0.000000  
285  1180.655148  1066.433797  942.630442  820.763300  706.991533  604.200726  
286     0.000000     0.000000    0.000000    0.000000    0.000000    0.000000  
287   201.784698   182.263231  161.104112  140.275910  120.831280  103.263397  

[288 rows x 27 columns]

In [59]:
# Now join the reshaped adoption results with the avoided cost data from df_yrs
# The join will match on: competition_group, electric_utility, gas_utility, building_type, efficiency_level, subgroup, market

# First, we need to add 'subgroup' to reshaped_adoption_results if it exists in df_yrs
# Get unique subgroups from df_yrs for each competition group
subgroup_mapping = df_yrs[['competition_group', 'electric_utility', 'gas_utility', 'building_type', 
                             'efficiency_level', 'subgroup']].drop_duplicates()

joined_results = {}

for name in reshaped_adoption_results.keys():
    df_reshaped = reshaped_adoption_results[name]
    
    # Merge with subgroup mapping to add subgroup column
    df_with_subgroup = df_reshaped.merge(
        subgroup_mapping,
        on=['competition_group', 'electric_utility', 'gas_utility', 'building_type', 'efficiency_level'],
        how='left'
    )
    
    print(f"\n{name.capitalize()} with subgroups shape: {df_with_subgroup.shape}")
    print(f"Columns: {df_with_subgroup.columns.tolist()}")
    
    # Now join with df_yrs to get avoided costs
    # Get relevant columns from df_yrs (exclude time-based adoption columns, keep cost/benefit columns)
    cost_benefit_cols = [col for col in df_yrs.columns if not col.startswith('adopt_t_')]
    df_yrs_costs = df_yrs[cost_benefit_cols].drop_duplicates()
    
    df_joined = df_with_subgroup.merge(
        df_yrs_costs,
        on=['competition_group', 'electric_utility', 'gas_utility', 'building_type', 'efficiency_level', 'subgroup', 'market'],
        how='left'
    )
    
    joined_results[name] = df_joined
    print(f"\n{name.capitalize()} joined with costs shape: {df_joined.shape}")
    display(df_joined)

# Store for later use
print("\n" + "="*80)
print("Join completed successfully!")


Tech with subgroups shape: (288, 28)
Columns: ['competition_group', 'electric_utility', 'gas_utility', 'building_type', 'efficiency_level', 'measure_life_(yrs)', 'market', 'adopt_t_0', 'adopt_t_1', 'adopt_t_10', 'adopt_t_11', 'adopt_t_12', 'adopt_t_13', 'adopt_t_14', 'adopt_t_15', 'adopt_t_16', 'adopt_t_17', 'adopt_t_18', 'adopt_t_19', 'adopt_t_2', 'adopt_t_3', 'adopt_t_4', 'adopt_t_5', 'adopt_t_6', 'adopt_t_7', 'adopt_t_8', 'adopt_t_9', 'subgroup']

Tech joined with costs shape: (288, 133)


competition_group electric_utility     gas_utility     building_type  \
0       refrigeration             none            none      multi_family   
1       refrigeration             none            none      multi_family   
2       refrigeration             none            none   multi_family_li   
3       refrigeration             none            none   multi_family_li   
4       refrigeration             none            none     single_family   
..                ...              ...             ...               ...   
283        whole_home   test_utility_2  test_utility_2   multi_family_li   
284        whole_home   test_utility_2  test_utility_2     single_family   
285        whole_home   test_utility_2  test_utility_2     single_family   
286        whole_home   test_utility_2  test_utility_2  single_family_li   
287        whole_home   test_utility_2  test_utility_2  single_family_li   

    efficiency_level  measure_life_(yrs)_x  market  adopt_t_0   adopt_t_1  \
0          efficient                  10.0  ret_er        0.0    0.000000   
1              top10                  10.0  ret_er        0.0    0.000000   
2          efficient                  10.0  ret_er        0.0    0.000000   
3              top10                  10.0  ret_er        0.0    0.000000   
4          efficient                  10.0  ret_er        0.0    0.000000   
..               ...                   ...     ...        ...         ...   
283            top10                  30.0     rob        0.0   11.666667   
284        efficient                  30.0     rob        0.0    0.000000   
285            top10                  30.0     rob        0.0  458.333333   
286        efficient                  30.0     rob        0.0    0.000000   
287            top10                  30.0     rob        0.0   78.333333   

     adopt_t_10  ...  trc_bcr  sct_cost  sct_benefit  sct_bcr  rim_cost  \
0      0.000000  ...      NaN       NaN          NaN      NaN       NaN   
1      0.000000  ...      NaN       NaN          NaN      NaN       NaN   
2      0.000000  ...      NaN       NaN          NaN      NaN       NaN   
3      0.000000  ...      NaN       NaN          NaN      NaN       NaN   
4      0.000000  ...      NaN       NaN          NaN      NaN       NaN   
..          ...  ...      ...       ...          ...      ...       ...   
283   13.066517  ...      NaN       NaN          NaN      NaN       NaN   
284    0.000000  ...      NaN       NaN          NaN      NaN       NaN   
285  513.327468  ...      NaN       NaN          NaN      NaN       NaN   
286    0.000000  ...      NaN       NaN          NaN      NaN       NaN   
287   87.732331  ...      NaN       NaN          NaN      NaN       NaN   

     rim_benefit  rim_bcr  pct_cost  pct_benefit  pct_bcr  
0            NaN      NaN       NaN          NaN      NaN  
1            NaN      NaN       NaN          NaN      NaN  
2            NaN      NaN       NaN          NaN      NaN  
3            NaN      NaN       NaN          NaN      NaN  
4            NaN      NaN       NaN          NaN      NaN  
..           ...      ...       ...          ...      ...  
283          NaN      NaN       NaN          NaN      NaN  
284          NaN      NaN       NaN          NaN      NaN  
285          NaN      NaN       NaN          NaN      NaN  
286          NaN      NaN       NaN          NaN      NaN  
287          NaN      NaN       NaN          NaN      NaN  

[288 rows x 133 columns]


Competition with subgroups shape: (288, 28)
Columns: ['competition_group', 'electric_utility', 'gas_utility', 'building_type', 'efficiency_level', 'measure_life_(yrs)', 'market', 'adopt_t_0', 'adopt_t_1', 'adopt_t_10', 'adopt_t_11', 'adopt_t_12', 'adopt_t_13', 'adopt_t_14', 'adopt_t_15', 'adopt_t_16', 'adopt_t_17', 'adopt_t_18', 'adopt_t_19', 'adopt_t_2', 'adopt_t_3', 'adopt_t_4', 'adopt_t_5', 'adopt_t_6', 'adopt_t_7', 'adopt_t_8', 'adopt_t_9', 'subgroup']

Competition joined with costs shape: (288, 133)


competition_group electric_utility     gas_utility     building_type  \
0       refrigeration             none            none      multi_family   
1       refrigeration             none            none      multi_family   
2       refrigeration             none            none   multi_family_li   
3       refrigeration             none            none   multi_family_li   
4       refrigeration             none            none     single_family   
..                ...              ...             ...               ...   
283        whole_home   test_utility_2  test_utility_2   multi_family_li   
284        whole_home   test_utility_2  test_utility_2     single_family   
285        whole_home   test_utility_2  test_utility_2     single_family   
286        whole_home   test_utility_2  test_utility_2  single_family_li   
287        whole_home   test_utility_2  test_utility_2  single_family_li   

    efficiency_level  measure_life_(yrs)_x  market  adopt_t_0   adopt_t_1  \
0          efficient                  10.0  ret_er        0.0    0.000000   
1              top10                  10.0  ret_er        0.0    0.000000   
2          efficient                  10.0  ret_er        0.0    0.000000   
3              top10                  10.0  ret_er        0.0    0.000000   
4          efficient                  10.0  ret_er        0.0    0.000000   
..               ...                   ...     ...        ...         ...   
283            top10                  30.0     rob        0.0    0.000000   
284        efficient                  30.0     rob        0.0  458.333333   
285            top10                  30.0     rob        0.0    0.000000   
286        efficient                  30.0     rob        0.0   78.333333   
287            top10                  30.0     rob        0.0    0.000000   

     adopt_t_10  ...  trc_bcr  sct_cost  sct_benefit  sct_bcr  rim_cost  \
0      0.000000  ...      NaN       NaN          NaN      NaN       NaN   
1      0.000000  ...      NaN       NaN          NaN      NaN       NaN   
2      0.000000  ...      NaN       NaN          NaN      NaN       NaN   
3      0.000000  ...      NaN       NaN          NaN      NaN       NaN   
4      0.000000  ...      NaN       NaN          NaN      NaN       NaN   
..          ...  ...      ...       ...          ...      ...       ...   
283    0.000000  ...      NaN       NaN          NaN      NaN       NaN   
284  513.327468  ...      NaN       NaN          NaN      NaN       NaN   
285    0.000000  ...      NaN       NaN          NaN      NaN       NaN   
286   87.732331  ...      NaN       NaN          NaN      NaN       NaN   
287    0.000000  ...      NaN       NaN          NaN      NaN       NaN   

     rim_benefit  rim_bcr  pct_cost  pct_benefit  pct_bcr  
0            NaN      NaN       NaN          NaN      NaN  
1            NaN      NaN       NaN          NaN      NaN  
2            NaN      NaN       NaN          NaN      NaN  
3            NaN      NaN       NaN          NaN      NaN  
4            NaN      NaN       NaN          NaN      NaN  
..           ...      ...       ...          ...      ...  
283          NaN      NaN       NaN          NaN      NaN  
284          NaN      NaN       NaN          NaN      NaN  
285          NaN      NaN       NaN          NaN      NaN  
286          NaN      NaN       NaN          NaN      NaN  
287          NaN      NaN       NaN          NaN      NaN  

[288 rows x 133 columns]


Join completed successfully!


In [61]:
# now we just multiply the avoided cost columns by the adoption columns for each time period
# For each adopt_t_<year> column, multiply it by all numeric cost/benefit columns
# and create new columns with the format: <metric_name>_<year>

final_results = {}

for name in joined_results.keys():
    df_joined = joined_results[name].copy()
    
    # Identify adoption time columns (adopt_t_2026, adopt_t_2027, etc.)
    adopt_cols = [col for col in df_joined.columns if col.startswith('adopt_t_')]
    
    # Identify avoided cost/benefit columns (all numeric columns that aren't adopt_t or measure_life)
    # Exclude ID columns and other non-metric columns
    id_cols = ['competition_group', 'electric_utility', 'gas_utility', 'building_type', 
               'efficiency_level', 'market', 'subgroup', 'measure_life_(yrs)']
    
    # Get all numeric columns
    numeric_cols = df_joined.select_dtypes(include=[np.number]).columns.tolist()
    
    # Filter to get only cost/benefit metric columns (exclude adopt_t and measure_life)
    cost_benefit_cols = [col for col in numeric_cols 
                         if not col.startswith('adopt_t_') 
                         and col != 'measure_life_(yrs)']
    
    print(f"\n{name.capitalize()} - Cost/benefit columns to multiply:")
    print(cost_benefit_cols[:10], "..." if len(cost_benefit_cols) > 10 else "")
    print(f"Total: {len(cost_benefit_cols)} metrics")
    
    print(f"\n{name.capitalize()} - Time periods:")
    print(adopt_cols)
    
    # Create all new columns at once using a dictionary (more efficient than adding one by one)
    new_cols_dict = {}
    
    # For each time period, multiply adoption by each cost/benefit metric
    for adopt_col in adopt_cols:
        # Extract year from column name (adopt_t_2026 -> 2026)
        year = adopt_col.replace('adopt_t_', '')
        
        # Multiply each cost/benefit column by this adoption column
        for metric_col in cost_benefit_cols:
            new_col_name = f"{metric_col}_{year}"
            new_cols_dict[new_col_name] = df_joined[metric_col] * df_joined[adopt_col]
    
    # Create a new DataFrame from the dictionary and concatenate with original
    new_cols_df = pd.DataFrame(new_cols_dict, index=df_joined.index)
    df_joined = pd.concat([df_joined, new_cols_df], axis=1)
    
    # Store the result
    final_results[name] = df_joined
    
    print(f"\n{name.capitalize()} final shape: {df_joined.shape}")
    print(f"Added {len(cost_benefit_cols) * len(adopt_cols)} new dollar columns")
    
    # Show sample of new columns
    new_cols = [col for col in df_joined.columns if any(col.endswith(f"_{adopt_cols[0].replace('adopt_t_', '')}") for adopt_col in adopt_cols[:1])]
    print(f"\nSample new columns for first year:")
    print(new_cols[:10])
    
    display(df_joined)

print("\n" + "="*80)
print("Dollar calculations completed!")


Tech - Cost/benefit columns to multiply:
['measure_life_(yrs)_x', 'measure_life_(yrs)_y', 'initial_count', 'count', 'id', 'incremental_cost_(usd)', 'annual_oandm_savings_(usd)', 'annual_energy_saved_(kwh)', 'water_savings_(gallons)', 'energy_impact_1'] ...
Total: 88 metrics

Tech - Time periods:
['adopt_t_0', 'adopt_t_1', 'adopt_t_10', 'adopt_t_11', 'adopt_t_12', 'adopt_t_13', 'adopt_t_14', 'adopt_t_15', 'adopt_t_16', 'adopt_t_17', 'adopt_t_18', 'adopt_t_19', 'adopt_t_2', 'adopt_t_3', 'adopt_t_4', 'adopt_t_5', 'adopt_t_6', 'adopt_t_7', 'adopt_t_8', 'adopt_t_9']

Tech final shape: (288, 1893)
Added 1760 new dollar columns

Sample new columns for first year:
['adopt_t_0', 'measure_life_(yrs)_x_0', 'measure_life_(yrs)_y_0', 'initial_count_0', 'count_0', 'id_0', 'incremental_cost_(usd)_0', 'annual_oandm_savings_(usd)_0', 'annual_energy_saved_(kwh)_0', 'water_savings_(gallons)_0']


competition_group electric_utility     gas_utility     building_type  \
0       refrigeration             none            none      multi_family   
1       refrigeration             none            none      multi_family   
2       refrigeration             none            none   multi_family_li   
3       refrigeration             none            none   multi_family_li   
4       refrigeration             none            none     single_family   
..                ...              ...             ...               ...   
283        whole_home   test_utility_2  test_utility_2   multi_family_li   
284        whole_home   test_utility_2  test_utility_2     single_family   
285        whole_home   test_utility_2  test_utility_2     single_family   
286        whole_home   test_utility_2  test_utility_2  single_family_li   
287        whole_home   test_utility_2  test_utility_2  single_family_li   

    efficiency_level  measure_life_(yrs)_x  market  adopt_t_0   adopt_t_1  \
0          efficient                  10.0  ret_er        0.0    0.000000   
1              top10                  10.0  ret_er        0.0    0.000000   
2          efficient                  10.0  ret_er        0.0    0.000000   
3              top10                  10.0  ret_er        0.0    0.000000   
4          efficient                  10.0  ret_er        0.0    0.000000   
..               ...                   ...     ...        ...         ...   
283            top10                  30.0     rob        0.0   11.666667   
284        efficient                  30.0     rob        0.0    0.000000   
285            top10                  30.0     rob        0.0  458.333333   
286        efficient                  30.0     rob        0.0    0.000000   
287            top10                  30.0     rob        0.0   78.333333   

     adopt_t_10  ...  trc_bcr_9  sct_cost_9  sct_benefit_9  sct_bcr_9  \
0      0.000000  ...        NaN         NaN            NaN        NaN   
1      0.000000  ...        NaN         NaN            NaN        NaN   
2      0.000000  ...        NaN         NaN            NaN        NaN   
3      0.000000  ...        NaN         NaN            NaN        NaN   
4      0.000000  ...        NaN         NaN            NaN        NaN   
..          ...  ...        ...         ...            ...        ...   
283   13.066517  ...        NaN         NaN            NaN        NaN   
284    0.000000  ...        NaN         NaN            NaN        NaN   
285  513.327468  ...        NaN         NaN            NaN        NaN   
286    0.000000  ...        NaN         NaN            NaN        NaN   
287   87.732331  ...        NaN         NaN            NaN        NaN   

     rim_cost_9  rim_benefit_9  rim_bcr_9  pct_cost_9  pct_benefit_9  \
0           NaN            NaN        NaN         NaN            NaN   
1           NaN            NaN        NaN         NaN            NaN   
2           NaN            NaN        NaN         NaN            NaN   
3           NaN            NaN        NaN         NaN            NaN   
4           NaN            NaN        NaN         NaN            NaN   
..          ...            ...        ...         ...            ...   
283         NaN            NaN        NaN         NaN            NaN   
284         NaN            NaN        NaN         NaN            NaN   
285         NaN            NaN        NaN         NaN            NaN   
286         NaN            NaN        NaN         NaN            NaN   
287         NaN            NaN        NaN         NaN            NaN   

     pct_bcr_9  
0          NaN  
1          NaN  
2          NaN  
3          NaN  
4          NaN  
..         ...  
283        NaN  
284        NaN  
285        NaN  
286        NaN  
287        NaN  

[288 rows x 1893 columns]


Competition - Cost/benefit columns to multiply:
['measure_life_(yrs)_x', 'measure_life_(yrs)_y', 'initial_count', 'count', 'id', 'incremental_cost_(usd)', 'annual_oandm_savings_(usd)', 'annual_energy_saved_(kwh)', 'water_savings_(gallons)', 'energy_impact_1'] ...
Total: 88 metrics

Competition - Time periods:
['adopt_t_0', 'adopt_t_1', 'adopt_t_10', 'adopt_t_11', 'adopt_t_12', 'adopt_t_13', 'adopt_t_14', 'adopt_t_15', 'adopt_t_16', 'adopt_t_17', 'adopt_t_18', 'adopt_t_19', 'adopt_t_2', 'adopt_t_3', 'adopt_t_4', 'adopt_t_5', 'adopt_t_6', 'adopt_t_7', 'adopt_t_8', 'adopt_t_9']

Competition final shape: (288, 1893)
Added 1760 new dollar columns

Sample new columns for first year:
['adopt_t_0', 'measure_life_(yrs)_x_0', 'measure_life_(yrs)_y_0', 'initial_count_0', 'count_0', 'id_0', 'incremental_cost_(usd)_0', 'annual_oandm_savings_(usd)_0', 'annual_energy_saved_(kwh)_0', 'water_savings_(gallons)_0']

Competition final shape: (288, 1893)
Added 1760 new dollar columns

Sample new columns f

competition_group electric_utility     gas_utility     building_type  \
0       refrigeration             none            none      multi_family   
1       refrigeration             none            none      multi_family   
2       refrigeration             none            none   multi_family_li   
3       refrigeration             none            none   multi_family_li   
4       refrigeration             none            none     single_family   
..                ...              ...             ...               ...   
283        whole_home   test_utility_2  test_utility_2   multi_family_li   
284        whole_home   test_utility_2  test_utility_2     single_family   
285        whole_home   test_utility_2  test_utility_2     single_family   
286        whole_home   test_utility_2  test_utility_2  single_family_li   
287        whole_home   test_utility_2  test_utility_2  single_family_li   

    efficiency_level  measure_life_(yrs)_x  market  adopt_t_0   adopt_t_1  \
0          efficient                  10.0  ret_er        0.0    0.000000   
1              top10                  10.0  ret_er        0.0    0.000000   
2          efficient                  10.0  ret_er        0.0    0.000000   
3              top10                  10.0  ret_er        0.0    0.000000   
4          efficient                  10.0  ret_er        0.0    0.000000   
..               ...                   ...     ...        ...         ...   
283            top10                  30.0     rob        0.0    0.000000   
284        efficient                  30.0     rob        0.0  458.333333   
285            top10                  30.0     rob        0.0    0.000000   
286        efficient                  30.0     rob        0.0   78.333333   
287            top10                  30.0     rob        0.0    0.000000   

     adopt_t_10  ...  trc_bcr_9  sct_cost_9  sct_benefit_9  sct_bcr_9  \
0      0.000000  ...        NaN         NaN            NaN        NaN   
1      0.000000  ...        NaN         NaN            NaN        NaN   
2      0.000000  ...        NaN         NaN            NaN        NaN   
3      0.000000  ...        NaN         NaN            NaN        NaN   
4      0.000000  ...        NaN         NaN            NaN        NaN   
..          ...  ...        ...         ...            ...        ...   
283    0.000000  ...        NaN         NaN            NaN        NaN   
284  513.327468  ...        NaN         NaN            NaN        NaN   
285    0.000000  ...        NaN         NaN            NaN        NaN   
286   87.732331  ...        NaN         NaN            NaN        NaN   
287    0.000000  ...        NaN         NaN            NaN        NaN   

     rim_cost_9  rim_benefit_9  rim_bcr_9  pct_cost_9  pct_benefit_9  \
0           NaN            NaN        NaN         NaN            NaN   
1           NaN            NaN        NaN         NaN            NaN   
2           NaN            NaN        NaN         NaN            NaN   
3           NaN            NaN        NaN         NaN            NaN   
4           NaN            NaN        NaN         NaN            NaN   
..          ...            ...        ...         ...            ...   
283         NaN            NaN        NaN         NaN            NaN   
284         NaN            NaN        NaN         NaN            NaN   
285         NaN            NaN        NaN         NaN            NaN   
286         NaN            NaN        NaN         NaN            NaN   
287         NaN            NaN        NaN         NaN            NaN   

     pct_bcr_9  
0          NaN  
1          NaN  
2          NaN  
3          NaN  
4          NaN  
..         ...  
283        NaN  
284        NaN  
285        NaN  
286        NaN  
287        NaN  

[288 rows x 1893 columns]


Dollar calculations completed!


In [ ]:
# Save this final results to pickle and CSV files for both tech and competition scenarios
for name in final_results.keys():
    df_final = final_results[name]
    output_pkl = f"050_output/{name}_final_dollar_results.pkl"
    output_csv = f"050_output/{name}_final_dollar_results.csv"
    
    df_final.to_pickle(output_pkl)
    df_final.to_csv(output_csv, index=False)
    output_pkl_2 = f"060_input/{name}_final_dollar_results.pkl"
    output_csv_2 = f"060_input/{name}_final_dollar_results.csv"
    
    df_final.to_pickle(output_pkl_2)
    df_final.to_csv(output_csv_2, index=False)
    


Saved tech final results to:
  - 050_output/tech_final_dollar_results.pkl
  - 050_output/tech_final_dollar_results.csv
  Shape: (288, 1893)

Saved competition final results to:
  - 050_output/competition_final_dollar_results.pkl
  - 050_output/competition_final_dollar_results.csv
  Shape: (288, 1893)

Saved competition final results to:
  - 050_output/competition_final_dollar_results.pkl
  - 050_output/competition_final_dollar_results.csv
  Shape: (288, 1893)

